# LFW Knowledge Graphy

- add name and description info from Google KG

In [158]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
import math
from glob import glob
from random import randint
import time

import numpy as np
import pandas as pd
%matplotlib inline
import matplotlib.pyplot as plt

import sys
sys.path.append('/work/megapixels_dev/megapixels/')
from app.utils import file_utils

In [159]:
import datetime
import requests
import json
import urllib

In [160]:
DATA_STORE = '/data_store_nas/'
dir_dataset = join(DATA_STORE, 'datasets/people/lfw')
fp_names = join(dir_dataset, 'lfw_names_gendered.csv')

In [161]:
# load names
df_names = pd.read_csv(fp_names)
names = df_names.to_dict('index')
list(names.values())[:2]

[{'gender': 'f', 'images': 1, 'name': 'AJ Cook'},
 {'gender': 'm', 'images': 1, 'name': 'AJ Lamas'}]

In [162]:
api_key = open('/work/megapixels_dev/3rdparty/knowledge-graph-api/.api_key').read()

def get_knowledge(q, api_key):
  service_url = 'https://kgsearch.googleapis.com/v1/entities:search'
  params = {
      'query': q,
      'limit': 5,
      'indent': True,
      'key': api_key,
      }
  url = service_url + '?' + urllib.parse.urlencode(params)  # TODO: use requests
  response = json.loads(urllib.request.urlopen(url).read())
  response = response.get('itemListElement', [])
  if len(response) > 0:
    result = response[0].get('result', [])
    result['score'] = response[0]['resultScore']
    return result
  else:
    return []

In [163]:
# test
q = 'AJ Cook'
r = get_knowledge(q, api_key)
print(r['description'])
print(r['name'])
print(r['url'])
print(r['score'])

Canadian actress
A. J. Cook
http://www.ajcookofficial.com
274.55481


In [165]:
# augment LFW CSV
for i in range(60):
  try:
    delay = 15
    keys = [('description','description'), ('name', 'name_kg'), ('url', 'url'), ('score', 'score')]
    for idx, item in names.items():
      # check for empties unset
      print(item['name'])
      try:
        _ = item['name_kg']
        continue
      except:
        pass
      # check for empties with None
      try:
        a,b,c = item['real_name'], item['description'], item['url']
        if a or b or c:
          continue
      except:
        pass
      kgr = get_knowledge(item['name'], api_key)
      for k1, k2 in keys:
        try:
          names[idx][k2] = kgr[k1]
        except:
          names[idx][k2] = ''
          #print('no {} data for {}'.format(k1, item['name']))
          pass
      #if idx % 10 == 0:
      txt = 'got: {} ({})'.format(item['name'], names[idx]['score'])
      time.sleep(1)
      txt += ', {} / {}, {:.2f}.'.format(idx, len(names), idx / len(names))
      print(txt)
  except Exception as e:
    print(e, item['name'])
    time.sleep(60)
    pass

AJ Cook
AJ Lamas
Aaron Eckhart
Aaron Guiel
Aaron Patterson
Aaron Peirsol
Aaron Pena
Aaron Sorkin
Aaron Tippin
Abba Eban
Abbas Kiarostami
Abdel Aziz Al-Hakim
Abdel Madi Shabneh
Abdel Nasser Assidi
Abdoulaye Wade
Abdul Majeed Shobokshi
Abdul Rahman
Abdulaziz Kamilov
Abdullah
Abdullah Ahmad Badawi
Abdullah Gul
Abdullah Nasseef
Abdullah al-Attiyah
got: Abdullah al-Attiyah (278.300262), 22 / 5749, 0.00.
Abdullatif Sener
got: Abdullatif Sener (483.411591), 23 / 5749, 0.00.
Abel Aguilar
got: Abel Aguilar (535.476624), 24 / 5749, 0.00.
Abel Pacheco
got: Abel Pacheco (380.46637), 25 / 5749, 0.00.
Abid Hamid Mahmud Al-Tikriti
got: Abid Hamid Mahmud Al-Tikriti (460.515961), 26 / 5749, 0.00.
Abner Martinez
got: Abner Martinez (42.59869), 27 / 5749, 0.00.
Abraham Foxman
got: Abraham Foxman (371.363556), 28 / 5749, 0.00.
Aby Har-Even
got: Aby Har-Even (), 29 / 5749, 0.01.
Adam Ant
got: Adam Ant (604.570374), 30 / 5749, 0.01.
Adam Freier
got: Adam Freier (323.42807), 31 / 5749, 0.01.
Adam Herbert
got

got: Alex Wallau (279.806), 144 / 5749, 0.03.
Alex Zanardi
got: Alex Zanardi (573.799744), 145 / 5749, 0.03.
Alexa Loren
got: Alexa Loren (), 146 / 5749, 0.03.
Alexa Vega
got: Alexa Vega (609.285828), 147 / 5749, 0.03.
Alexander Downer
got: Alexander Downer (477.19986), 148 / 5749, 0.03.
Alexander Losyukov
got: Alexander Losyukov (226.954483), 149 / 5749, 0.03.
Alexander Lukashenko
got: Alexander Lukashenko (641.057373), 150 / 5749, 0.03.
Alexander Payne
got: Alexander Payne (585.464294), 151 / 5749, 0.03.
Alexander Rumyantsev
got: Alexander Rumyantsev (268.9758), 152 / 5749, 0.03.
Alexandra Jackson
got: Alexandra Jackson (180.769058), 153 / 5749, 0.03.
Alexandra Pelosi
got: Alexandra Pelosi (430.675751), 154 / 5749, 0.03.
Alexandra Rozovskaya
got: Alexandra Rozovskaya (), 155 / 5749, 0.03.
Alexandra Spann
got: Alexandra Spann (94.71981), 156 / 5749, 0.03.
Alexandra Stevenson
got: Alexandra Stevenson (453.363037), 157 / 5749, 0.03.
Alexandra Vodjanikova
got: Alexandra Vodjanikova (4.48

got: Andrew Fastow (411.024475), 268 / 5749, 0.05.
Andrew Firestone
got: Andrew Firestone (423.148407), 269 / 5749, 0.05.
Andrew Gilligan
got: Andrew Gilligan (352.598022), 270 / 5749, 0.05.
Andrew Jarecki
got: Andrew Jarecki (404.26416), 271 / 5749, 0.05.
Andrew Luster
got: Andrew Luster (365.909698), 272 / 5749, 0.05.
Andrew Niccol
got: Andrew Niccol (472.229431), 273 / 5749, 0.05.
Andrew Sabey
got: Andrew Sabey (), 274 / 5749, 0.05.
Andrew Shutley
got: Andrew Shutley (), 275 / 5749, 0.05.
Andrew Weissmann
got: Andrew Weissmann (388.029327), 276 / 5749, 0.05.
Andrew Wetzler
got: Andrew Wetzler (), 277 / 5749, 0.05.
Andrzej Tyszkiewicz
got: Andrzej Tyszkiewicz (227.113113), 278 / 5749, 0.05.
Andy Benes
got: Andy Benes (422.881226), 279 / 5749, 0.05.
Andy Bryant
got: Andy Bryant (180.072433), 280 / 5749, 0.05.
Andy Dick
got: Andy Dick (624.710083), 281 / 5749, 0.05.
Andy Garcia
got: Andy Garcia (682.709045), 282 / 5749, 0.05.
Andy Graves
got: Andy Graves (152.717667), 283 / 5749, 0.05.

got: Arthur Martinez (259.701141), 395 / 5749, 0.07.
Artieas Shanks
got: Artieas Shanks (), 396 / 5749, 0.07.
Arturo Gatti
got: Arturo Gatti (499.617828), 397 / 5749, 0.07.
Arye Mekel
got: Arye Mekel (106.82254), 398 / 5749, 0.07.
Asa Hutchinson
got: Asa Hutchinson (489.737518), 399 / 5749, 0.07.
Ascencion Barajas
got: Ascencion Barajas (), 400 / 5749, 0.07.
Ashanti
got: Ashanti (66.886459), 401 / 5749, 0.07.
Ashlea Talbot
got: Ashlea Talbot (), 402 / 5749, 0.07.
Ashley Judd
got: Ashley Judd (643.355835), 403 / 5749, 0.07.
Ashley Olsen
got: Ashley Olsen (585.24939), 404 / 5749, 0.07.
Ashley Postell
got: Ashley Postell (310.611359), 405 / 5749, 0.07.
Ashraf Alasmar
got: Ashraf Alasmar (), 406 / 5749, 0.07.
Ashraf Ghani
got: Ashraf Ghani (754.314636), 407 / 5749, 0.07.
Ashton Kutcher
got: Ashton Kutcher (716.098816), 408 / 5749, 0.07.
Asif Ali Zardari
got: Asif Ali Zardari (806.705994), 409 / 5749, 0.07.
Asif Hanif
got: Asif Hanif (15.397957), 410 / 5749, 0.07.
Askar Akayev
got: Askar Ak

got: Biljana Plavsic (462.925049), 522 / 5749, 0.09.
Bill Belichick
got: Bill Belichick (664.852783), 523 / 5749, 0.09.
Bill Bradley
got: Bill Bradley (799.277344), 524 / 5749, 0.09.
Bill Butler
got: Bill Butler (388.855652), 525 / 5749, 0.09.
Bill Byrne
got: Bill Byrne (327.139923), 526 / 5749, 0.09.
Bill Callahan
got: Bill Callahan (571.816345), 527 / 5749, 0.09.
Bill Carmody
got: Bill Carmody (344.10788), 528 / 5749, 0.09.
Bill Cartwright
got: Bill Cartwright (481.17099), 529 / 5749, 0.09.
Bill Clancy
got: Bill Clancy (185.492401), 530 / 5749, 0.09.
Bill Clinton
got: Bill Clinton (1794.225586), 531 / 5749, 0.09.
Bill Curry
got: Bill Curry (456.828186), 532 / 5749, 0.09.
Bill Doba
got: Bill Doba (311.572754), 533 / 5749, 0.09.
Bill Duffey
got: Bill Duffey (20.873724), 534 / 5749, 0.09.
Bill Elliott
got: Bill Elliott (594.102417), 535 / 5749, 0.09.
Bill Fennelly
got: Bill Fennelly (321.104156), 536 / 5749, 0.09.
Bill Frist
got: Bill Frist (491.725525), 537 / 5749, 0.09.
Bill Gates
got

...

Laura Ziskin
Laurel Clark
Lauren Hutton
Lauren Killian
Laurence Fishburne
Laurence Tribe
Laurent Gbagbo
Laurent Jalabert
Laurent Woulzy
Laurie Chan
Laurie Hobbs
Laurie Laychak
Laurie Pirtle
Lawrence Di Rita
Lawrence Foley
Lawrence MacAulay
Lawrence Roberts
Lawrence Vito
Lazaro Castro
LeAnn Rimes
LeBron James
LeRoy Millette Jr
Lea Fastow
Leah Remini
Leander Paes
Leandrinho Barbosa
Leandro Andrade
Leandro Garcia
Lech Walesa
Lee Ann Knight
Lee Ann Terlaji
Lee Ann Womack
Lee Baca
Lee Byung-woong
Lee Chang-dong
Lee Hoi-chang
Lee Hong-ki
Lee Hyung-taik
Lee Jun
Lee Nam-shin
Lee Soo-hyuck
Lee Tae-sik
Lee Yeo-jin
Lee Yuan-tseh
Leigh Winchell
Leisel Jones
Lela Rochon
Leland Chapman
Lemuel Montulo
Len Jenoff
Lena Katina
Lena Olin
Lene Espersen
Leni Bjorklund
Lennart Johansson
Lennox Lewis
Lenny Kravitz
Lenny Wilkens
Leo Mullin
Leo Ramirez
Leon Barmore
Leon LaPorte
Leon Lai
Leon Silver
Leonard Glick
Leonard Hamilton
Leonard Schrank
Leonardo Del Vecchio
Leonardo DiCaprio
Leonardo Fernandez
Leonid K

Jean-Sebastien Giguere
Jean Brumley
Jean Carnahan
Jean Charest
Jean Chretien
Jean Nagel
Jean Todt
Jeane Kirkpatrick
Jeanette Gray
Jeanette Stauffer
Jeanne Anne Schroeder
Jeanne Moreau
Jeannette Biedermann
Jeb Bush
Jeff Bridges
Jeff Bzdelik
Jeff Dederian
Jeff Feldman
Jeff George
Jeff Hornacek
Jeff Roehm
Jeff Schiffner
Jeff Van Gundy
Jeff Weaver
Jefferson Perez
Jeffery Hendren
Jeffery Strelzin
Jeffrey Archer
Jeffrey Ashby
Jeffrey Donaldson
Jeffrey Immelt
Jeffrey Jones
Jeffrey Katzenberg
Jeffrey Pfeffer
Jeffrey Scott Postell
Jelena Dokic
Jen Bice
Jen Schefft
Jenna Elfman
Jennette Bradley
Jennie Finch
Jennie Garth
Jennifer Aniston
Jennifer Capriati
Jennifer Connelly
Jennifer Furminger
Jennifer Garner
Jennifer Granholm
Jennifer Gratz
Jennifer Keller
Jennifer Lopez
Jennifer Love Hewitt
Jennifer McCoy
Jennifer Murray
Jennifer Pena
Jennifer Reilly
Jennifer Renee Short
Jennifer Rodriguez
Jennifer Thompson
Jennifer Tilly
Jenny Romero
Jens Lehmann
Jeong Se-hyun
Jerelle Kraus
Jeremy Fogel
Jeremy G

Florencia Kirchner
Florencia Macri
Floyd Keith
Floyd Mayweather
Fran Drescher
Frances Fisher
Francesco Totti
Francis Collins
Francis Crick
Francis Ford Coppola
Francis George
Francis Mer
Francis Ricciardone
Francisco Flores
Francisco Garcia
Francisco Maturana
Francisco Santos
Francisco Urenda
Franck Cerutti
Franco Cangele
Franco Dragone
Franco Frattini
Francois Botha
Francois Ozon
Francois Pienaar
Frank Abagnale Jr
Frank Beamer
Frank Bell
Frank Cassell
Frank Coraci
Frank Dunham Jr
Frank Griswold
Frank Hilldrup
Frank Hsieh
Frank Keating
Frank Lautenberg
Frank Marshall
Frank Murkowski
Frank Pallone
Frank Schmoekel
Frank Shea
Frank Sinatra
Frank Solich
Frank Stallone
Frank Taylor
Frank Van Ecke
Frank Wycheck
Frank Zappa
Franklin Brown
Franklin Damann
Franko Simatovic
Franz Beckenbauer
Franz Fischler
Franz Gsell
Franz Muentefering
Fred Durst
Fred Eckhard
Fred Funk
Fred Huff
Fred Rogers
Fred Swan
Fred Thompson
Fred Wilpon
Freda Black
Freddy Garcia
Freddy Vasques Kinchokpe
Frederick Madden
F

Bashar Assad
Baz Luhrmann
Beatrice Dalle
Beatriz Merino
Beecher Ray Kirby
Begum Khaleda Zia
Bela Karolyi
Ben Affleck
Ben Betts
Ben Braun
Ben Broussard
Ben Cahoon
Ben Chandler
Ben Cohen
Ben Curtis
Ben Davis
Ben Glisan
Ben Howland
Ben Kingsley
Ben Lee
Ben Stein
Ben Wallace
Benazir Bhutto
Benedita da Silva
Benicio Del Toro
Benito Santiago
Benjamin Bratt
Benjamin Franklin
Benjamin Martinez
Benjamin McKenzie
Benjamin Netanyahu
Benjamin Neulander
Bernadette Peters
Bernard Ebbers
Bernard Giraudeau
Bernard Kerik
Bernard Landry
Bernard Law
Bernard Lord
Bernard Siegel
Bernardo Segura
Bernice Wong
Bertie Ahern
Bertrand Bonello
Bertrand Delanoe
Beth Blough
Beth Jones
Betsy Coffin
Betsy Smith
Bettina Rheims
Betty Garrison
Betty Williams
Beyonce Knowles
Bianca Jagger
Bijan Darvish
Bijan Namdar Zangeneh
Bilal Erdogan
Biljana Plavsic
Bill Belichick
Bill Bradley
Bill Butler
Bill Byrne
Bill Callahan
Bill Carmody
Bill Cartwright
Bill Clancy
Bill Clinton
Bill Curry
Bill Doba
Bill Duffey
Bill Elliott
Bill 

Tony LaRussa
Tony Parker
Tony Shalhoub
Tony Stewart
Tonya Payne
Tora Takagi
Tori Amos
Torri Edwards
Toshi Izawa
Toshihiko Fukui
Toshimitsu Motegi
Toutai Kefu
Tracee Ellis Ross
Tracee Treadwell
Tracy McGrady
Tracy Wyle
Travis Rudolph
Trent Lott
Trevor McDonald
Trevor Watson
Trisha Meili
Trista Rehn
Tristan Gretzky
Troy Aikman
Troy Garity
Troy Hudson
Troy Jenkins
Troy Polamalu
Trudi Lacey
Tsutomu Takebe
Tubby Smith
Tuncay Sanli
Tung Chee-hwa
Turner Gill
Turner Stevenson
Ty Votaw
Tyler Grillo
Tyler Hamilton
Tyra Banks
Tyron Garner
Tyrone Medley
Tzipora Obziler
Uday Hussein
Ulrich Kueperkoch
Uma Thurman
Uri Lopolianski
Urmila Matondkar
Uthai Pimchaichon
Uzi Even
Uzi Landau
Vaclav Havel
Vaclav Klaus
Vadim Devyatovskiy
Vadim Strogalev
Vagit Alekperov
Val Ackerman
Valdas Adamkus
Valentina Cervi
Valentina Tereshkova
Valentino Rossi
Valeri Bure
Valerie Harper
Valerie Thwaites
Valery Giscard dEstaing
Valorie Brabazon
Van Hilley
Vanessa Incontrada
Vanessa Laine
Vanessa Redgrave
Vanessa Williams
V

In [166]:
names_bkup = names.copy()

In [167]:
# save to csv
fp_kg = join(dir_dataset, 'lfw_names_gender_kg_bkup.csv')
df_kg = pd.DataFrame.from_dict(list(names.values()))  # ignore the indices
df_kg.to_csv(fp_kg, index=False)

## Filter and Reduce

In [185]:
# load names
fp_names = join(dir_dataset, 'lfw_names_gender_kg_bkup.csv')
df_names = pd.read_csv(fp_names)
names = df_names.to_dict('index')
list(names.values())[:2]
names_copy = names.copy()

In [190]:
names_new = names.copy()
for idx, item in names_copy.items():
  score = names_new[idx].get('score', 0)
  if not score:
    score = 0
    
  # clean up
  if score < 50:
    
    try:
      names_new[idx].pop('description')
    except:
      pass
    
    try:
      names_new[idx].pop('name_kg')
    except:
      pass
    
    try:
      names_new[idx].pop('score')
    except:
      pass
    
  else:
    name_kg = str(names_new[idx].get('name_kg', ''))
    if len(name_kg) > 0:
      #names_new[idx]['name'] = names[idx]['name_kg']
      names_new[idx].pop('name_kg')
    names_new[idx].pop('score')
  names_new[idx].pop('url')

In [191]:
# save to csv
fp_kg = join(dir_dataset, 'lfw_names_gender_kg_min.csv')
df_kg = pd.DataFrame.from_dict(list(names_new.values()))  # ignore the indices
df_kg.to_csv(fp_kg, index=False)

```
Sample result: https://kgsearch.googleapis.com/v1/entities:search?query=taylor+swift&key=[]&limit=1&indent=True

{
  "@context": {
    "@vocab": "http://schema.org/",
    "goog": "http://schema.googleapis.com/",
    "EntitySearchResult": "goog:EntitySearchResult",
    "detailedDescription": "goog:detailedDescription",
    "resultScore": "goog:resultScore",
    "kg": "http://g.co/kg"
  },
  "@type": "ItemList",
  "itemListElement": [
    {
      "@type": "EntitySearchResult",
      "result": {
        "@id": "kg:/m/0dl567",
        "name": "Taylor Swift",
        "@type": [
          "Thing",
          "Person"
        ],
        "description": "Singer-songwriter",
        "image": {
          "contentUrl": "http://t1.gstatic.com/images?q=tbn:ANd9GcQmVDAhjhWnN2OWys2ZMO3PGAhupp5tN2LwF_BJmiHgi19hf8Ku",
          "url": "https://en.wikipedia.org/wiki/Taylor_Swift",
          "license": "http://creativecommons.org/licenses/by-sa/2.0"
        },
        "detailedDescription": {
          "articleBody": "Taylor Alison Swift is an American singer-songwriter.
          Raised in Wyomissing, Pennsylvania, she moved to Nashville, Tennessee, at the age of 14
          to pursue a career in country music. ",
          "url": "http://en.wikipedia.org/wiki/Taylor_Swift",
          "license": "https://en.wikipedia.org/wiki/Wikipedia:Text_of_Creative_Commons_Attribution-ShareAlike_3.0_Unported_License"
        },
        "url": "http://www.taylorswift.com/"
      },
      "resultScore": 884.364868
    }
  ]
}
```

In [90]:
api_key = open('/work/megapixels_dev/3rdparty/knowledge-graph-api/.api_key').read()

def get_knowledge_all(q, api_key):
  service_url = 'https://kgsearch.googleapis.com/v1/entities:search'
  params = {
      'query': q,
      'limit': 5,
      'indent': True,
      'key': api_key,
      }
  url = service_url + '?' + urllib.parse.urlencode(params)  # TODO: use requests
  response = json.loads(urllib.request.urlopen(url).read())
  return response

In [91]:
response = get_knowledge_all("Asmaa al-Assad", api_key)

In [93]:
from pprint import pprint

In [100]:
pprint(response['itemListElement'][0]['resultScore'])

241.345016
